drop all cols with strings and unvaluable info like index
Always make sure it is sorted correctly by time and station
edit time of year with cos/sin "encode"
df['day_of_year'] = df['valid_time'].dt.dayofyear
?? subrtract a row in setting forecast hours ??

In [2]:
%load_ext autoreload
%autoreload 2
import sys

# instead of creating a package using setup.py or building from a docker/singularity file,
# import the sister directory of src code to be called on in notebook.
# This keeps the notebook free from code to only hold visualizations and is easier to test
# It also helps keep the state of variables clean such that cells aren't run out of order with a mysterious state
sys.path.append("..")

In [3]:
from comet_ml import Experiment
from comet_ml.integration.pytorch import log_model
from comet_ml import Optimizer
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torch import nn
import os
import datetime as dt
from dateutil.parser import parse
from tqdm import tqdm
import re
import emd
import statistics as st
from multiprocessing import Process


In [4]:
def col_drop(df):
    df = df.drop(columns=["day_of_year", "flag", "station", "latitude", 'longitude', 't2m', 'sh2', 'd2m', 'r2', 'u10', 'v10', 'tp', 'mslma', 'orog', 'tcc', 'asnow', 'cape', 'dswrf', 'dlwrf', 'gh', 'u_total', 'u_dir', 'new_tp', 'lat', 'lon', 'elev', 'tair', 'ta9m', 'td', 'relh', 'srad', 'pres', 'mslp', 'wspd_sonic', 'wmax_sonic', 'wdir_sonic', 'precip_total','snow_depth', 'day_of_year', 'day_of_year_sin', 'day_of_year_cos', '11_nlcd', '21_nlcd', '22_nlcd', '23_nlcd', '24_nlcd', '31_nlcd', '41_nlcd', '42_nlcd', '43_nlcd', '52_nlcd', '71_nlcd', '81_nlcd','82_nlcd','90_nlcd','95_nlcd','19_aspect', '21_aspect','24_aspect', '27_aspect', '28_aspect', '22_aspect', '23_aspect', '25_aspect', '26_aspect', '31_aspect', '33_aspect', '32_aspect', '34_aspect', '38_aspect', 'std_elev', 'variance_elev', 'skew_elev', 'med_dist_elev'])
    df = df[df.columns.drop(list(df.filter(regex="time")))]
    df = df[df.columns.drop(list(df.filter(regex="station")))]
    df = df[df.columns.drop(list(df.filter(regex="tair")))]
    df = df[df.columns.drop(list(df.filter(regex="ta9m")))]
    df = df[df.columns.drop(list(df.filter(regex="td")))]
    df = df[df.columns.drop(list(df.filter(regex="relh")))]
    df = df[df.columns.drop(list(df.filter(regex="srad")))]
    df = df[df.columns.drop(list(df.filter(regex="pres")))]
    df = df[df.columns.drop(list(df.filter(regex="wspd")))]
    df = df[df.columns.drop(list(df.filter(regex="wmax")))]
    df = df[df.columns.drop(list(df.filter(regex="wdir")))]
    df = df[df.columns.drop(list(df.filter(regex="precip_total")))]
    df = df[df.columns.drop(list(df.filter(regex="snow_depth")))]

    return df

In [5]:
def get_flag(hrrr_df):
    """
    Create a flag column in the input DataFrame indicating consecutive hourly time intervals.

    This function takes a DataFrame containing weather data for different stations, with a 'station' column
    representing the station ID and a 'valid_time' column containing timestamps of the weather data.
    It calculates the time difference between consecutive timestamps for each station and marks it as 'True'
    in a new 'flag' column if the difference is exactly one hour, indicating consecutive hourly time intervals.
    Otherwise, it marks the 'flag' as 'False'.

    Parameters:
    hrrr_df (pandas.DataFrame): Input DataFrame containing weather data for different stations.

    Returns:
    pandas.DataFrame: The input DataFrame with an additional 'flag' column indicating consecutive hourly time intervals.
    
    Example:
      station           valid_time   flag
    0        1 2023-08-01 00:00:00   True
    1        1 2023-08-01 01:00:00   False
    2        1 2023-08-01 03:00:00   False
    3        2 2023-08-01 08:00:00   True
    4        2 2023-08-01 09:00:00   False
    5        2 2023-08-01 11:00:00   True
    """

    # Get unique station IDs
    stations_ls = hrrr_df["station"].unique()

    # Define a time interval of one hour
    one_hour = dt.timedelta(hours=1)

    # Initialize a list to store flags for each time interval
    flag_ls = []

    # Loop through each station and calculate flags for consecutive hourly time intervals
    for station in stations_ls:
        # Filter DataFrame for the current station
        df = hrrr_df[hrrr_df["station"] == station]
        
        # Get the list of valid_time timestamps for the current station
        time_ls = df["valid_time"].tolist()

        # Compare each timestamp with the next one to determine consecutive intervals
        for now, then in zip(time_ls, time_ls[1:]):
            if now + one_hour == then:
                flag_ls.append(True)
            else:
                flag_ls.append(False)

    # Append an extra True to indicate the last time interval (since it has no next timestamp for comparison)
    flag_ls.append(True)

    # Add the 'flag' column to the DataFrame
    hrrr_df["flag"] = flag_ls

    return hrrr_df

In [6]:
def nwp_error(target, station, df):
    vars_dict = {
        "t2m": "tair",
        "mslma": "pres",
    }
    nysm_var = vars_dict.get(target)

    df["target_error"] = df[f"{target}_{station}"] - df[f"{nysm_var}_{station}"]
    return df

In [7]:
def encode(data, col, max_val):
    data[col + "_sin"] = np.sin(2 * np.pi * data[col] / max_val)
    data[col + "_cos"] = np.cos(2 * np.pi * data[col] / max_val)

    return data

In [8]:
def format_climate_df(data_path):
    """
    Formats a climate data file located at the specified `data_path` into a pandas DataFrame.

    Args:
        data_path (str): The file path for the climate data file.

    Returns:
        pandas.DataFrame: A DataFrame containing the climate data, with the first column renamed to "year".
    """
    raw_index = np.loadtxt(f"{data_path}")
    cl_index = pd.DataFrame(raw_index)
    cl_index = cl_index.rename(columns={0: "year"})
    return cl_index

In [9]:
def get_clim_indexes(df):
    """
    Fetch climate indexes data and add corresponding index values to the input DataFrame.

    This function takes a DataFrame (`df`) containing weather data with a 'valid_time' column representing
    timestamps. It reads climate indexes data from text files in the specified directory and extracts index
    values corresponding to the month and year of each timestamp in the DataFrame. The extracted index values
    are then added to the DataFrame with new columns named after each index.

    Parameters:
    df (pandas.DataFrame): Input DataFrame containing weather data with a 'valid_time' column.

    Returns:
    pandas.DataFrame: The input DataFrame with additional columns for each climate index containing their values.
    """

    clim_df_path = '/home/aevans/nwp_bias/src/correlation/data/indexes/'
    directory = os.listdir(clim_df_path)

    # Loop through each file in the specified directory
    for d in directory:
        if d.endswith(".txt"):
            # Read the climate index data from the file and format it into a DataFrame
            clim_df = format_climate_df(f'{clim_df_path}{d}')
            index_name = d.split('.')[0]

            clim_ind_ls = []
            for t, _ in enumerate(df['valid_time']):
                time_obj = df['valid_time'].iloc[t]
                dt_object = parse(str(time_obj))
                year = dt_object.strftime('%Y')
                month = dt_object.strftime('%m')
                # Filter the climate DataFrame to get data for the specific year
                df1 = clim_df.loc[clim_df['year'] == int(year)]
                df1 = df1.drop(columns='year')
                row_list = df1.values
                keys = df1.keys()
                key_vals = keys.tolist()

                # Extract the index value corresponding to the month of the timestamp
                the_list = []
                for n, _ in enumerate(key_vals):
                    val1 = key_vals[n]
                    val2 = row_list[0, n]
                    tup = (val1, val2)
                    the_list.append(tup)
                for k, r in the_list:
                    if str(k).zfill(2) == month:
                        clim_ind_ls.append(r)

            # Add the climate index values as a new column in the DataFrame
            df[index_name] = clim_ind_ls

    return df

In [10]:
df = pd.read_parquet(
    "/home/aevans/nwp_bias/src/machine_learning/data/clean_parquets/nysm_cats/cleaned_rough_lstm_nysmcat_Western Plateau.parquet"
)
df = df.dropna()

In [11]:
df

valid_time                time station_ADDI  latitude_ADDI  \
0     2018-01-01 03:00:00 2018-01-01 01:00:00         ADDI      42.045955   
1     2018-01-01 04:00:00 2018-01-01 02:00:00         ADDI      42.045955   
2     2018-01-01 05:00:00 2018-01-01 03:00:00         ADDI      42.045955   
3     2018-01-01 06:00:00 2018-01-01 04:00:00         ADDI      42.045955   
4     2018-01-01 07:00:00 2018-01-01 05:00:00         ADDI      42.045955   
...                   ...                 ...          ...            ...   
22486 2022-12-31 19:00:00 2022-12-31 17:00:00         ADDI      42.045955   
22487 2022-12-31 20:00:00 2022-12-31 18:00:00         ADDI      42.045955   
22488 2022-12-31 21:00:00 2022-12-31 19:00:00         ADDI      42.045955   
22489 2022-12-31 22:00:00 2022-12-31 20:00:00         ADDI      42.045955   
22490 2022-12-31 23:00:00 2022-12-31 21:00:00         ADDI      42.045955   

       longitude_ADDI   t2m_ADDI  sh2_ADDI   d2m_ADDI    r2_ADDI  u10_ADDI  \
0          -77.218867 -19.199194   0.00068 -21.993216  76.800003  3.321081   
1          -77.218867 -19.118689   0.00068 -21.918570  76.500000  3.298830   
2          -77.218867 -19.439062   0.00065 -22.570868  73.800003  2.992857   
3          -77.218867 -19.760291   0.00063 -22.821158  74.400002  3.115693   
4          -77.218867 -19.860175   0.00062 -22.993704  74.099998  3.268302   
...               ...        ...       ...        ...        ...       ...   
22486      -77.218867  11.485986   0.00710   8.142847  80.300003  0.073768   
22487      -77.218867  10.447198   0.00676   7.376611  80.400002 -0.416093   
22488      -77.218867   9.658258   0.00709   8.101648  88.000000  0.234075   
22489      -77.218867   9.118555   0.00711   8.145227  92.000000  0.285457   
22490      -77.218867   8.866113   0.00724   8.439722  94.900002  0.120182   

       ...  26_aspect_RAND  31_aspect_RAND  33_aspect_RAND  32_aspect_RAND  \
0      ...        5.217391             0.0             0.0             0.0   
1      ...        5.217391             0.0             0.0             0.0   
2      ...        5.217391             0.0             0.0             0.0   
3      ...        5.217391             0.0             0.0             0.0   
4      ...        5.217391             0.0             0.0             0.0   
...    ...             ...             ...             ...             ...   
22486  ...        5.217391             0.0             0.0             0.0   
22487  ...        5.217391             0.0             0.0             0.0   
22488  ...        5.217391             0.0             0.0             0.0   
22489  ...        5.217391             0.0             0.0             0.0   
22490  ...        5.217391             0.0             0.0             0.0   

       34_aspect_RAND  38_aspect_RAND  std_elev_RAND  variance_elev_RAND  \
0                 0.0             0.0      77.124478         5896.461701   
1                 0.0             0.0      77.124478         5896.461701   
2                 0.0             0.0      77.124478         5896.461701   
3                 0.0             0.0      77.124478         5896.461701   
4                 0.0             0.0      77.124478         5896.461701   
...               ...             ...            ...                 ...   
22486             0.0             0.0      77.124478         5896.461701   
22487             0.0             0.0      77.124478         5896.461701   
22488             0.0             0.0      77.124478         5896.461701   
22489             0.0             0.0      77.124478         5896.461701   
22490             0.0             0.0      77.124478         5896.461701   

       skew_elev_RAND  med_dist_elev_RAND  
0            0.569549          405.940002  
1            0.569549          405.940002  
2            0.569549          405.940002  
3            0.569549          405.940002  
4            0.569549          405.940002  
...               ...                 .

In [12]:
for k in df.keys():
    print(k)

valid_time
time
station_ADDI
latitude_ADDI
longitude_ADDI
t2m_ADDI
sh2_ADDI
d2m_ADDI
r2_ADDI
u10_ADDI
v10_ADDI
tp_ADDI
mslma_ADDI
orog_ADDI
tcc_ADDI
asnow_ADDI
cape_ADDI
dswrf_ADDI
dlwrf_ADDI
gh_ADDI
u_total_ADDI
u_dir_ADDI
new_tp_ADDI
lat_ADDI
lon_ADDI
elev_ADDI
tair_ADDI
ta9m_ADDI
td_ADDI
relh_ADDI
srad_ADDI
pres_ADDI
mslp_ADDI
wspd_sonic_ADDI
wmax_sonic_ADDI
wdir_sonic_ADDI
precip_total_ADDI
snow_depth_ADDI
day_of_year_ADDI
day_of_year_sin_ADDI
day_of_year_cos_ADDI
11_nlcd_ADDI
21_nlcd_ADDI
22_nlcd_ADDI
23_nlcd_ADDI
24_nlcd_ADDI
31_nlcd_ADDI
41_nlcd_ADDI
42_nlcd_ADDI
43_nlcd_ADDI
52_nlcd_ADDI
71_nlcd_ADDI
81_nlcd_ADDI
82_nlcd_ADDI
90_nlcd_ADDI
95_nlcd_ADDI
19_aspect_ADDI
21_aspect_ADDI
24_aspect_ADDI
27_aspect_ADDI
28_aspect_ADDI
22_aspect_ADDI
23_aspect_ADDI
25_aspect_ADDI
26_aspect_ADDI
31_aspect_ADDI
33_aspect_ADDI
32_aspect_ADDI
34_aspect_ADDI
38_aspect_ADDI
std_elev_ADDI
variance_elev_ADDI
skew_elev_ADDI
med_dist_elev_ADDI
time_ADDI
station
latitude
longitude
t2m
sh2
d2m
r2
u10

In [13]:
# columns to reintigrate back into the df after model is done running
cols_to_carry = ["valid_time", "flag"]

In [14]:
# edit dataframe
df = df[df.columns.drop(list(df.filter(regex="day")))]
df["day_of_year"] = df["valid_time"].dt.dayofyear
df = encode(df, "day_of_year", 366)

/tmp/tmp.qdG0W8bpe1/ipykernel_435253/2776712703.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["day_of_year"] = df["valid_time"].dt.dayofyear
/tmp/tmp.qdG0W8bpe1/ipykernel_435253/3070891546.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[col + "_sin"] = np.sin(2 * np.pi * data[col] / max_val)
/tmp/tmp.qdG0W8bpe1/ipykernel_435253/3070891546.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

In [15]:
df = nwp_error("t2m", "ADDI", df)

/tmp/tmp.qdG0W8bpe1/ipykernel_435253/1678785731.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["target_error"] = df[f"{target}_{station}"] - df[f"{nysm_var}_{station}"]


In [16]:
df = get_clim_indexes(df)

/tmp/tmp.qdG0W8bpe1/ipykernel_435253/1509060441.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[index_name] = clim_ind_ls
/tmp/tmp.qdG0W8bpe1/ipykernel_435253/1509060441.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[index_name] = clim_ind_ls
/tmp/tmp.qdG0W8bpe1/ipykernel_435253/1509060441.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pa

In [17]:
df = get_flag(df)

/tmp/tmp.qdG0W8bpe1/ipykernel_435253/1480764800.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  hrrr_df["flag"] = flag_ls


In [18]:
new_df = col_drop(df)

In [19]:
def normalize_df(df):
    the_df = df.dropna()
    for (k,r) in the_df.items():
        if len(the_df[k].unique()) == 1:
            org_str = str(k)
            my_str = org_str[:-5]
            vals = the_df.filter(regex=my_str)
            vals = vals.loc[0].tolist()
            means = st.mean(vals)
            stdevs = st.pstdev(vals)
            the_df[k] = (the_df[k] - means) / stdevs

            the_df = the_df.fillna(0)
        if re.search('t2m|sh2|d2m|r2|u10|v10|tp|mslma|tcc|asnow|cape|dswrf|dlwrf|gh|utotal|u_dir|new_tp', k):

            ind_val = the_df.columns.get_loc(k)
            x = the_df[k]
            imf = emd.sift.sift(x)
            the_df = the_df.drop(columns=k)
            for i in range(imf.shape[1]):
                imf_ls = imf[:,i].tolist()
                # Inserting the column at the
                # beginning in the DataFrame
                my_loc = ind_val + i
                the_df.insert(loc = (my_loc),
                        column = f'{k}_imf_{i}',
                        value = imf_ls)      
            
        else:
            
            means = st.mean(the_df[k])
            stdevs = st.pstdev(the_df[k])
            the_df[k] = (the_df[k] - means) / stdevs
    
    final_df = the_df.fillna(0)
    print("!!! Dropping Columns !!!")
    final_df = final_df[final_df.columns.drop(list(final_df.filter(regex="latitude")))]
    final_df = final_df[final_df.columns.drop(list(final_df.filter(regex="longitude")))]
    final_df = final_df[final_df.columns.drop(list(final_df.filter(regex="u_total")))]
    final_df = final_df[final_df.columns.drop(list(final_df.filter(regex="mslp")))]
    final_df = final_df[final_df.columns.drop(list(final_df.filter(regex="orog")))]
    new_features = list(final_df.columns.difference(['target_error']))
    print('---normalize successful---')
    return final_df, new_features 

## create train and test set

In [20]:
target_sensor = "target_error"
features = list(new_df.columns.difference([target_sensor]))

forecast_lead = 12
target = f"{target_sensor}_lead_{forecast_lead}"

new_df[target] = new_df[target_sensor].shift(-forecast_lead)
new_df = new_df.iloc[:-forecast_lead]

In [21]:
new_df.keys()

Index(['latitude_ADDI', 'longitude_ADDI', 't2m_ADDI', 'sh2_ADDI', 'd2m_ADDI',
       'r2_ADDI', 'u10_ADDI', 'v10_ADDI', 'tp_ADDI', 'mslma_ADDI',
       ...
       'amo', 'amoc', 'enso4', 'enso_1_2', 'pna', 'enso3', 'ao', 'pdo', 'nao',
       'target_error_lead_12'],
      dtype='object', length=515)

In [22]:
new_df.head()

latitude_ADDI  longitude_ADDI   t2m_ADDI  sh2_ADDI   d2m_ADDI    r2_ADDI  \
0      42.045955      -77.218867 -19.199194   0.00068 -21.993216  76.800003   
1      42.045955      -77.218867 -19.118689   0.00068 -21.918570  76.500000   
2      42.045955      -77.218867 -19.439062   0.00065 -22.570868  73.800003   
3      42.045955      -77.218867 -19.760291   0.00063 -22.821158  74.400002   
4      42.045955      -77.218867 -19.860175   0.00062 -22.993704  74.099998   

   u10_ADDI  v10_ADDI  tp_ADDI  mslma_ADDI  ...   amo  amoc  enso4  enso_1_2  \
0  3.321081 -2.272873    0.001    103034.0  ...  0.15  2.12  -0.44     -1.12   
1  3.298830 -1.821096    0.000    103019.0  ...  0.15  2.12  -0.44     -1.12   
2  2.992857 -0.877062    0.000    103027.0  ...  0.15  2.12  -0.44     -1.12   
3  3.115693 -0.789671    0.000    103071.0  ...  0.15  2.12  -0.44     -1.12   
4  3.268302 -0.054269    0.001    103052.0  ...  0.15  2.12  -0.44     -1.12   

    pna  enso3     ao  pdo   nao  target_error_lead_12  
0 -0.14  -1.18 -0.281  0.7  1.17             -0.013050  
1 -0.14  -1.18 -0.281  0.7  1.17              0.538113  
2 -0.14  -1.18 -0.281  0.7  1.17              0.320462  
3 -0.14  -1.18 -0.281  0.7  1.17              0.073639  
4 -0.14  -1.18 -0.281  0.7  1.17             -0.233670  

[5 rows x 515 columns]

# Normalize

In [23]:
the_df, new_features = normalize_df(new_df)

/home/aevans/miniconda3/lib/python3.9/site-packages/emd/support.py:228: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  out_args[idx] = out_args[idx][:, np.newaxis]
<frozen importlib._bootstrap>:228: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject
/home/aevans/miniconda3/lib/python3.9/site-packages/emd/support.py:228: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  out_args[idx] = out_args[idx][:, np.newaxis]
/home/aevans/miniconda3/lib/python3.9/site-packages/emd/support.py:228: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Conve

!!! Dropping Columns !!!
---normalize successful---


In [24]:
the_df.head()

t2m_ADDI_imf_0  t2m_ADDI_imf_1  t2m_ADDI_imf_2  t2m_ADDI_imf_3  \
0        0.170504        2.071257        0.130187       -0.666658   
1        0.244174        2.082879       -0.061888       -0.408810   
2        0.004027        1.874030       -0.173222       -0.102947   
3       -0.180427        1.485543       -0.209059        0.245777   
4       -0.122428        0.967830       -0.178884        0.631789   

   t2m_ADDI_imf_4  t2m_ADDI_imf_5  t2m_ADDI_imf_6  t2m_ADDI_imf_7  \
0        0.677416       -7.863977       -4.560570       -8.645412   
1        0.544474       -7.810390       -4.553888       -8.643076   
2        0.414537       -7.755222       -4.547153       -8.640729   
3        0.287712       -7.698499       -4.540365       -8.638369   
4        0.164107       -7.640243       -4.533523       -8.635999   

   t2m_ADDI_imf_8  t2m_ADDI_imf_9  ...       amo      amoc     enso4  \
0        0.108108       -0.620050  ...  0.067979  0.881749 -0.475821   
1        0.107602       -0.619764  ...  0.067979  0.881749 -0.475821   
2        0.107096       -0.619479  ...  0.067979  0.881749 -0.475821   
3        0.106590       -0.619194  ...  0.067979  0.881749 -0.475821   
4        0.106085       -0.618908  ...  0.067979  0.881749 -0.475821   

   enso_1_2       pna     enso3        ao       pdo       nao  \
0 -0.834538  0.398206 -1.149837 -0.410731  0.691366  0.928738   
1 -0.834538  0.398206 -1.149837 -0.410731  0.691366  0.928738   
2 -0.834538  0.398206 -1.149837 -0.410731  0.691366  0.928738   
3 -0.834538  0.398206 -1.149837 -0.410731  0.691366  0.928738   
4 -0.834538  0.398206 -1.149837 -0.410731  0.691366  0.928738   

   target_error_lead_12  
0             -0.362324  
1              0.045431  
2             -0.115589  
3             -0.298190  
4             -0.525540  

[5 rows x 1776 columns]

In [25]:
for k in the_df.keys():
    print(k)

t2m_ADDI_imf_0
t2m_ADDI_imf_1
t2m_ADDI_imf_2
t2m_ADDI_imf_3
t2m_ADDI_imf_4
t2m_ADDI_imf_5
t2m_ADDI_imf_6
t2m_ADDI_imf_7
t2m_ADDI_imf_8
t2m_ADDI_imf_9
sh2_ADDI_imf_0
sh2_ADDI_imf_1
sh2_ADDI_imf_2
sh2_ADDI_imf_3
sh2_ADDI_imf_4
sh2_ADDI_imf_5
sh2_ADDI_imf_6
sh2_ADDI_imf_7
sh2_ADDI_imf_8
sh2_ADDI_imf_9
d2m_ADDI_imf_0
d2m_ADDI_imf_1
d2m_ADDI_imf_2
d2m_ADDI_imf_3
d2m_ADDI_imf_4
d2m_ADDI_imf_5
d2m_ADDI_imf_6
d2m_ADDI_imf_7
d2m_ADDI_imf_8
d2m_ADDI_imf_9
r2_ADDI_imf_0
r2_ADDI_imf_1
r2_ADDI_imf_2
r2_ADDI_imf_3
r2_ADDI_imf_4
r2_ADDI_imf_5
r2_ADDI_imf_6
r2_ADDI_imf_7
r2_ADDI_imf_8
u10_ADDI_imf_0
u10_ADDI_imf_1
u10_ADDI_imf_2
u10_ADDI_imf_3
u10_ADDI_imf_4
u10_ADDI_imf_5
u10_ADDI_imf_6
u10_ADDI_imf_7
u10_ADDI_imf_8
u10_ADDI_imf_9
v10_ADDI_imf_0
v10_ADDI_imf_1
v10_ADDI_imf_2
v10_ADDI_imf_3
v10_ADDI_imf_4
v10_ADDI_imf_5
v10_ADDI_imf_6
v10_ADDI_imf_7
v10_ADDI_imf_8
v10_ADDI_imf_9
tp_ADDI_imf_0
tp_ADDI_imf_1
tp_ADDI_imf_2
tp_ADDI_imf_3
tp_ADDI_imf_4
tp_ADDI_imf_5
tp_ADDI_imf_6
tp_ADDI_imf_7
tp_ADDI_imf_

In [26]:
length = len(the_df)

test_len = int(length * 0.75)

df_train = the_df.iloc[:test_len].copy()
df_test = the_df.iloc[test_len:].copy()

print("Test Set Fraction", len(df_test) / len(the_df))

Test Set Fraction 0.25001112149116955


## Normalize

In [27]:
for c in cols_to_carry:
    df_train[c] = df[c]
    df_test[c] = df[c]

In [28]:
df_train = df_train.fillna(0)
df_test = df_test.fillna(0)

## Create LSTM

In [29]:
class SequenceDataset(Dataset):
    def __init__(self, dataframe, target, features, sequence_length):
        self.dataframe = dataframe
        self.features = features
        self.target = target
        self.sequence_length = sequence_length
        self.y = torch.tensor(dataframe[target].values).float()
        self.X = torch.tensor(dataframe[features].values).float()

    def __len__(self):
        return self.X.shape[0]

    def __getitem__(self, i):
        keep_sample = self.dataframe.iloc[i]['flag']
        if i >= self.sequence_length - 1:
            i_start = i - self.sequence_length + 1
            x = self.X[i_start : (i + 1), :]
        else:
            padding = self.X[0].repeat(self.sequence_length - i - 1, 1)
            x = self.X[0 : (i + 1), :]
            x = torch.cat((padding, x), 0)

        return x, self.y[i], keep_sample


In [30]:
class ShallowRegressionLSTM(nn.Module):
    def __init__(self, num_sensors, hidden_units):
        super().__init__()
        self.num_sensors = num_sensors  # this is the number of features
        self.hidden_units = hidden_units
        self.num_layers = 3

        self.lstm = nn.LSTM(
            input_size=num_sensors,
            hidden_size=hidden_units,
            batch_first=True,
            num_layers=self.num_layers,
        )
        self.linear = nn.Linear(in_features=self.hidden_units, out_features=1)

    def forward(self, x):
        batch_size = x.shape[0]
        h0 = torch.zeros(
            self.num_layers, batch_size, self.hidden_units
        ).requires_grad_()
        c0 = torch.zeros(
            self.num_layers, batch_size, self.hidden_units
        ).requires_grad_()

        _, (hn, _) = self.lstm(x, (h0, c0))
        out = self.linear(
            hn[0]
        ).flatten()  # First dim of Hn is num_layers, which is set to 1 above.

        return out

In [31]:
class EarlyStopper:
    def __init__(self, patience, min_delta=0):
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.min_validation_loss = np.inf

    def early_stop(self, validation_loss):
        if validation_loss < self.min_validation_loss:
            self.min_validation_loss = validation_loss
            self.counter = 0
        elif validation_loss > (self.min_validation_loss + self.min_delta):
            self.counter += 1
            if self.counter >= self.patience:
                return True
        return False

In [32]:
def remove_elements_from_batch(X, y, s):
    cond = (np.where(s))
    return X[cond], y[cond], s[cond]

In [33]:
def train_model(data_loader, model, loss_function, optimizer):
    num_batches = len(data_loader)
    total_loss = 0
    model.train()

    with tqdm(data_loader, unit = 'batch') as tepoch:
        for X, y, s in tepoch:
            X, y, s = remove_elements_from_batch(X, y, s)
            #X, y = (X.to(self.config.DEVICE),
                    #y.to(self.config.DEVICE))
            output = model(X)
            loss = loss_function(output, y)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            total_loss += loss.item()

    # loss
    avg_loss = total_loss / num_batches
    print(f"Train loss: {avg_loss}")
    return avg_loss


def test_model(data_loader, model, loss_function):
    num_batches = len(data_loader)
    total_loss = 0

    model.eval()
    with torch.no_grad():
        with tqdm(data_loader, unit = 'batch') as tepoch:
            for X, y, s in tepoch:
                X, y, s = remove_elements_from_batch(X, y, s)
                # X, y = (X.to(self.config.DEVICE),
                #         y.to(self.config.DEVICE))
                output = model(X)
                total_loss += loss_function(output, y).item()

    # loss
    avg_loss = total_loss / num_batches
    print(f"Test loss: {avg_loss}")

    return avg_loss

In [34]:
# # define fit function here!
# def fit(learning_rate, steps, batch_size):
#     hyperparameters = {'learning_rate': learning_rate, 'steps': steps, "batch_size": batch_size}
#     test_loss, test_acc = train_new_model(hyperparameters)
#     return(test_loss, test_acc)

In [38]:
torch.manual_seed(101)
batch_size = 14
sequence_length = 18
learning_rate = 5e-4
num_hidden_units = 80

experiment = Experiment(
    api_key="leAiWyR5Ck7tkdiHIT7n6QWNa",
    project_name="fh_2_hrrr",
    workspace="shmaronshmevans",
)
# Report multiple hyperparameters using a dictionary:
hyper_params = {
    "learning_rate": learning_rate,
    "steps": sequence_length,
    "batch_size": batch_size,
}

batch_size = batch_size
sequence_length = sequence_length

train_dataset = SequenceDataset(
    df_train, target=target, features=new_features, sequence_length=sequence_length
)
test_dataset = SequenceDataset(
    df_test, target=target, features=new_features, sequence_length=sequence_length
)

train_loader = DataLoader(train_dataset, batch_size, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size, shuffle=False)

X, y, s = next(iter(train_loader))

print("Features shape:", X.shape)
print("Target shape:", y.shape)

learning_rate = learning_rate
num_hidden_units = num_hidden_units

model = ShallowRegressionLSTM(num_sensors=len(new_features), hidden_units=num_hidden_units)
loss_function = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
early_stopper = EarlyStopper(patience=10, min_delta=0)


print("Untrained test\n--------")
test_model(test_loader, model, loss_function)
print()

for ix_epoch in range(5):
    print(f"Epoch {ix_epoch}\n---------")
    train_loss = train_model(train_loader, model, loss_function, optimizer=optimizer)
    val_loss = test_model(test_loader, model, loss_function)
    print()
    experiment.log_parameters(hyper_params)
    experiment.log_parameters('epoch', ix_epoch)
    if early_stopper.early_stop(val_loss):
        break

# Seamlessly log your Pytorch model
log_model(experiment, model, model_name="exp1")
experiment.end()

Features shape: torch.Size([14, 18, 1775])
Target shape: torch.Size([14])
Untrained test
--------


100%|██████████| 402/402 [00:18<00:00, 21.29batch/s]


Test loss: 0.9778211147510516

Epoch 0
---------


100%|██████████| 1205/1205 [01:06<00:00, 18.03batch/s]


Train loss: 0.9954619478635274


100%|██████████| 402/402 [00:11<00:00, 35.03batch/s]


Test loss: 1.0456439854428914

Epoch 1
---------


 47%|████▋     | 562/1205 [00:26<00:29, 21.52batch/s]

In [ ]:
df_train.head()

t2m_ADDI_imf_0  t2m_ADDI_imf_1  t2m_ADDI_imf_2  t2m_ADDI_imf_3  \
0        0.170504        2.071257        0.130187       -0.666658   
1        0.244174        2.082879       -0.061888       -0.408810   
2        0.004027        1.874030       -0.173222       -0.102947   
3       -0.180427        1.485543       -0.209059        0.245777   
4       -0.122428        0.967830       -0.178884        0.631789   

   t2m_ADDI_imf_4  t2m_ADDI_imf_5  t2m_ADDI_imf_6  t2m_ADDI_imf_7  \
0        0.677416       -7.863977       -4.560570       -8.645412   
1        0.544474       -7.810390       -4.553888       -8.643076   
2        0.414537       -7.755222       -4.547153       -8.640729   
3        0.287712       -7.698499       -4.540365       -8.638369   
4        0.164107       -7.640243       -4.533523       -8.635999   

   t2m_ADDI_imf_8  t2m_ADDI_imf_9  ...     enso4  enso_1_2       pna  \
0        0.108108       -0.620050  ... -0.475821 -0.834538  0.398206   
1        0.107602       -0.619764  ... -0.475821 -0.834538  0.398206   
2        0.107096       -0.619479  ... -0.475821 -0.834538  0.398206   
3        0.106590       -0.619194  ... -0.475821 -0.834538  0.398206   
4        0.106085       -0.618908  ... -0.475821 -0.834538  0.398206   

      enso3        ao       pdo       nao  target_error_lead_12  \
0 -1.149837 -0.410731  0.691366  0.928738             -0.362324   
1 -1.149837 -0.410731  0.691366  0.928738              0.045431   
2 -1.149837 -0.410731  0.691366  0.928738             -0.115589   
3 -1.149837 -0.410731  0.691366  0.928738             -0.298190   
4 -1.149837 -0.410731  0.691366  0.928738             -0.525540   

           valid_time  flag  
0 2018-01-01 03:00:00  True  
1 2018-01-01 04:00:00  True  
2 2018-01-01 05:00:00  True  
3 2018-01-01 06:00:00  True  
4 2018-01-01 07:00:00  True  

[5 rows x 1778 columns]

## Evaluate Model

In [ ]:
def predict(data_loader, model):
    output = torch.tensor([])
    model.eval()
    with torch.no_grad():
        for X, _, s  in data_loader:
            print(X)
            y_star = model(X)
            #print(y_star)
            output = torch.cat((output, y_star), 0)

    return output


train_eval_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=False)

ystar_col = "Model forecast"
df_train[ystar_col] = predict(train_eval_loader, model).numpy()
df_test[ystar_col] = predict(test_loader, model).numpy()
print(df_train[ystar_col])

df_out = pd.concat((df_train, df_test))[[target, ystar_col]]

for c in df_out.columns:
    vals = df_out[c].values.tolist()
    mean = st.mean(vals)
    std = st.pstdev(vals)
    df_out[c] = df_out[c] * std + mean

NameError: name 'DataLoader' is not defined

In [ ]:
df_out

target_error_lead_12  Model forecast
0                 -0.362324         0.03963
1                  0.045431         0.03963
2                 -0.115589         0.03963
3                 -0.298190         0.03963
4                 -0.525540         0.03963
...                     ...             ...
22474              0.136341         0.03963
22475              0.118983         0.03963
22476             -0.694566         0.03963
22477             -0.717479         0.03963
22478             -0.302743         0.03963

[22479 rows x 2 columns]

In [ ]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

pio.templates.default = "plotly_white"
plot_template = dict(
    layout=go.Layout(
        {"font_size": 18, "xaxis_title_font_size": 24, "yaxis_title_font_size": 24}
    )
)


fig = px.line(df_out, labels=dict(created_at="Date", value="Forecast Error"))
fig.add_vline(x=(length * 0.75), line_width=4, line_dash="dash")
fig.add_annotation(
    xref="paper", x=0.75, yref="paper", y=0.8, text="Test set start", showarrow=False
)
fig.update_layout(
    template=plot_template, legend=dict(orientation="h", y=1.02, title_text="")
)
fig.show()